In [1]:
# Here, we simulate the temperature evolution of a bar of length 0.3m (30cm)
# The bar is divided into three main sections of length 0.1m (10cm) with different thermal coefficients
# The simulation is performed via finite-difference-method by defining 300 silces of length Delta_x = 0.01m (1cm)
# Other dimensions of the bar are:
#  - height = 0.01m (1cm)
#  - depth  = 0.04m (4cm)
#
# The thermal diffusion is supposed to be homogeneous along y and z axis
# The implemented model is then a 1D model
#
# The thermal coefficients are considered to be constant, then to not vary wrt the material temeprature

In [ ]:
from scipy.integrate import solve_ivp
from thermal_model.thermal_model_nonlinear import thermal_model_nonlinear
from thermal_model.thermal_model_solver_ivp import thermal_model_solver_ivp
import numpy as np

Ntsmp  = 15 

t_init = 0
t_end  = 15
T_a    = 20+273.15
q_ext  = 1e3

Delta_t = 1e-3

# Initial temperature of bar
T_init    = T_a*np.ones( 300 )

# Environment temperature evolution: [ time | temperature ]
T_a_input = np.zeros((Ntsmp,2))
T_a_input[:,0] = np.linspace( t_init , t_end , Ntsmp )
T_a_input[:,1] = T_a

# Input heat evolution: [ time | heat ]
q_ext_input = np.zeros((Ntsmp,2))
q_ext_input[:,0] = np.linspace( t_init , t_end , Ntsmp )
q_ext_input[:,1] = np.concatenate( ( 1e5*np.ones(5) , 1e2*np.ones(5), np.zeros(5) ) )

In [3]:
# Simulation 1: nonlinear model
mthd = 'Radau'
sol = solve_ivp( thermal_model_nonlinear , [ t_init , t_end ] , T_init , method = mthd , args = ( T_a_input , q_ext_input ) )
print("Non-linear model simulation ended")

Non-linear model simulation ended


In [ ]:
# Simulation 2: linearized model with Backward Euler step
sim_time , T_sim_L_BE = thermal_model_solver_ivp( [ t_init , t_end ] , Delta_t , T_init , T_a_input , q_ext_input , 'BE_linear' )
print("Linearized model + BE method ended")

In [ ]:
# TO ADD ALL THE STEEPEST DESCENT OPTIONS

# Simulation 3: linearized model with Backward Euler step and steepest descent method
sim_time , T_sim_L_BE_SD = thermal_model_solver_ivp( [ t_init , t_end ] , Delta_t , T_init , T_a_input , q_ext_input , 'no' )
print("Linearized model + BE method + Steepest descent ended")

Linearized model + BE method ended


In [ ]:
import plotly.graph_objects as go

# Interpolate with respect to the same time vector
T_sim_NL = np.zeros(T_sim_L_BE.shape)
for i in range(300):
    T_sim_NL[i,:] = np.interp( sim_time , sol.t ,  sol.y[i,:] )

# Plot results
# Nonlinear model result average
avg_NL = np.zeros( (3 , len(sim_time)) )
for i in range(len(sim_time)):
    avg_NL[0,i] = np.mean( T_sim_NL[0:100,i] )
    avg_NL[1,i] = np.mean( T_sim_NL[100:200,i] )
    avg_NL[2,i] = np.mean( T_sim_NL[200:300,i] )

# Linear model result average - BE direct
avg_L_BE = np.zeros( (3 , len(sim_time)) )
for i in range(len(sim_time)):
    avg_L_BE[0,i] = np.mean( T_sim_L_BE[0:100,i] )
    avg_L_BE[1,i] = np.mean( T_sim_L_BE[100:200,i] )
    avg_L_BE[2,i] = np.mean( T_sim_L_BE[200:300,i] )

# Linear model result average - BE + Steepest descent
avg_L_BE_SD = np.zeros( (3 , len(sim_time)) )
for i in range(len(sim_time)):
    avg_L_BE_SD[0,i] = np.mean( T_sim_L_BE_SD[0:100,i] )
    avg_L_BE_SD[1,i] = np.mean( T_sim_L_BE_SD[100:200,i] )
    avg_L_BE_SD[2,i] = np.mean( T_sim_L_BE_SD[200:300,i] )


fig = go.Figure()
fig.add_scatter( x = sim_time , y = avg_NL[0,:] , line = dict(color='blue') )
fig.add_scatter( x = sim_time , y = avg_NL[1,:] , line = dict(color='green') )
fig.add_scatter( x = sim_time , y = avg_NL[2,:] , line = dict(color='orange') )
fig.add_scatter( x = sim_time , y = avg_L_BE[0,:] , line = dict(color='blue',dash='dash') )
fig.add_scatter( x = sim_time , y = avg_L_BE[1,:] , line = dict(color='green',dash='dash') )
fig.add_scatter( x = sim_time , y = avg_L_BE[2,:] , line = dict(color='orange',dash='dash') )

# TO CHANGE LINE TYPE
fig.add_scatter( x = sim_time , y = avg_L_BE_SD[0,:] , line = dict(color='blue',dash='dash') )
fig.add_scatter( x = sim_time , y = avg_L_BE_SD[1,:] , line = dict(color='green',dash='dash') )
fig.add_scatter( x = sim_time , y = avg_L_BE_SD[2,:] , line = dict(color='orange',dash='dash') )

fig.show()